In [ ]:
# ..... merge metacells within each stage - using MN auroc > 0.95 ..... #

In [4]:
library(igraph)

In [53]:
currstage = 'stage32'
mergedf = read.delim(paste0(currstage, '_cluster_from_metacell_de.csv'), sep = ',')
mergedf[1,]

cluster   metacell
1 cluster_1 1

In [54]:
topdf = read.delim(paste0(currstage, '_merge_cluster.csv'), sep = ',')
topdf[1,]

Study_ID.Celltype_1 Study_ID.Celltype_2 Mean_AUROC Match_type        
1 s10|cluster_59      s12|cluster_59      1          Reciprocal_top_hit

In [55]:
topdf$metacell1 <- sub('.*\\|', '', topdf[,1])
topdf$metacell2 <- sub('.*\\|', '', topdf[,2])
topdf[1,]

Study_ID.Celltype_1 Study_ID.Celltype_2 Mean_AUROC Match_type        
1 s10|cluster_59      s12|cluster_59      1          Reciprocal_top_hit
  metacell1  metacell2 
1 cluster_59 cluster_59

In [56]:
# metacell connectivity matrix
celltypes = sort(unique(mergedf$cluster))
celltypes = celltypes[!is.na(celltypes)]
cmat3 = matrix(0, nrow = length(celltypes), ncol = length(celltypes))
for(ii in 1:dim(topdf)[1]){
    c1 = match(topdf[ii,5], celltypes)
    c2 = match(topdf[ii,6], celltypes)
    cmat3[c1,c2] = 1
    cmat3[c2,c1] = 1
}
rownames(cmat3) <- celltypes
colnames(cmat3) <- celltypes

In [57]:
# get all possible connected nodes using igraph shortest_paths()
cmat4 <- shortest.paths(graph_from_adjacency_matrix(cmat3))
cmat4[4:6,4:6]

cluster_12 cluster_13 cluster_14
cluster_12   0        Inf        Inf       
cluster_13 Inf          0        Inf       
cluster_14 Inf        Inf          0

In [58]:
# get list of matched celltypes
celltypes2 = celltypes
list2 = data.frame(cluster = celltypes, elements = NA, num_elements = NA)
pb = txtProgressBar(min = 0, max = length(celltypes), initial = 0)
ctr = 1
df1 = c()

for(ii in 1:length(celltypes)){
    if(length(celltypes2)){
        ctype = celltypes2[1]
        ctype2 = c(ctype, names(which(cmat4[ctype,]!=Inf & cmat4[ctype,]>0)))
        list2$elements[ii] = paste(ctype2, collapse = ', ')
        list2$num_elements[ii] = length(ctype2)        
        celltypes2 <- setdiff(celltypes2, ctype2)
        
        # make full df
        temp = data.frame(cluster_new = rep(paste0('cluster_', ctr), length(ctype2)),
                                        cluster = ctype2)
        df1 = rbind(df1, temp)
        ctr = ctr + 1
    }
    setTxtProgressBar(pb, ii)
}
list2 <- list2[!is.na(list2$elements),]
length(celltypes)
dim(list2)
head(list2)
df1[1:3,]

[1] 64

[1] 49  3

cluster    elements   num_elements
1 cluster_1  cluster_1  1           
2 cluster_10 cluster_10 1           
3 cluster_11 cluster_11 1           
4 cluster_12 cluster_12 1           
5 cluster_13 cluster_13 1           
6 cluster_14 cluster_14 1

cluster_new cluster   
1 cluster_1   cluster_1 
2 cluster_2   cluster_10
3 cluster_3   cluster_11

In [59]:
mergedf$cluster_mn <- df1$cluster_new[match(mergedf$cluster, df1$cluster)]
length(unique(mergedf$cluster_mn))
mergedf[1,]

[1] 49

cluster   metacell cluster_mn
1 cluster_1 1        cluster_1

In [60]:
write.table(mergedf, file = paste0(currstage, '_cluster_from_metacell_MN.csv'),
            sep = ',', row.names = F, col.names = T, quote = F)